There are [two ways](https://arxiv.org/help/bulk_data) to access bulk metadata:
- API — Completed code, but will not use.
    - [User manual](https://arxiv.org/help/api/user-manual)
- OAI-PMH — This is the preferred way to bulk-download or keep an up-to-date copy of arXiv metadata.

In [155]:
import urllib, time, pandas as pd, numpy as np
from bs4 import BeautifulSoup
from enum import Enum

Get metadata from arXiv API:

In [278]:
# Specify categories to search
categories = [
    'astro-ph',     # general astrophysics
    'astro-ph.ga',  # astrophysics of galaxies
    'astro-ph.co',  # cosmology and nongalactic astrophysics
    'astro-ph.ep',  # earth and planetary astrophysics
    'astro-ph.he',  # high energy astrophysical phenomena
    'astro-ph.im',  # instrumentation and methods for astrophysics 
    'astro-ph.sr']  # solar and stellar astrophysics

results_per_page = 1000
rows = []

def get_metadata_from_arXiv_API():
    for category in categories:
        print('Getting metadata for articles within the ' + category + ' category...')
        # Search parameters
        search_query = 'cat:' + category
        startIndex = 0

        # Loop until total results reached
        while True:
            url = 'http://export.arxiv.org/api/query?search_query=' + search_query + '&start=' + str(startIndex) + '&max_results=' + str(results_per_page)
            results = urllib.request.urlopen(url).read()
            soup = BeautifulSoup(results, 'xml')

            if startIndex == 0:
                total_results = int(soup.find('opensearch:totalResults').string)

            # Get all entry tags
            entries = soup.find_all('entry')

            for entry in entries: 
                # Collect authors
                authors = []
                for author in entry.find_all('name'):
                    authors.append(author.string)
                author_str = ', '.join(authors)

                # Get DOI if it exists
                doi = entry.find('arxiv:doi')
                if doi:
                    doi = doi.string

                # Extract links if they exist
                doi_link = None
                pdf_link = None
                links = entry.find_all('link')
                for link in links:
                    link_title = link.get('title')
                    if link_title and link_title == 'doi':
                        doi_link = link['href']
                    elif link_title and link_title == 'pdf':
                        pdf_link = link['href']

                # Get journal if it exists
                journal = entry.find('arxiv:journal_ref')
                if journal:
                    journal = journal.string

                # Get comment if it exists
                comment = entry.find('arxiv:comment')
                if comment:
                    comment = comment.string

                row = {
                    'id': entry.id.string,
                    'updated': entry.updated.string,
                    'published': entry.published.string,
                    'title': entry.title.string,
                    'summary': entry.summary.string,
                    'authors': author_str,
                    'doi': doi,
                    'doi_link': doi_link,
                    'journal': journal,
                    'pdf_link': pdf_link,
                    'category': entry.find('arxiv:primary_category')['term'],
                    'comment': comment
                }
                rows.append(row)

                # Quit looping if we have gotten all results
                # print(str(len(rows)) + ' of ' + str(total_results) + '...')
            if len(rows) == total_results:
                print()
                break
            else:
                print(str(len(rows)) +'/' + str(total_results) + '...')
                startIndex += results_per_page
                time.sleep(3) # recommended to sleep

In [279]:
start = time.time()
get_metadata_from_arXiv_API()
end = time.time()
print(str(end - start) + ' seconds')

Getting metadata for articles within the astro-ph category
1000/105380...
2000/105380...
3000/105380...
4000/105380...
5000/105380...
6000/105380...
7000/105380...
8000/105380...
9000/105380...
10000/105380...
11000/105380...
11000/105380...
12000/105380...
13000/105380...
14000/105380...
15000/105380...
16000/105380...
17000/105380...
18000/105380...
18000/105380...
19000/105380...
20000/105380...
21000/105380...
22000/105380...
23000/105380...
23600/105380...
24600/105380...
25600/105380...
26600/105380...
27600/105380...
28600/105380...
29600/105380...
30600/105380...
31600/105380...
32600/105380...
33600/105380...
34600/105380...
35600/105380...
36600/105380...
37600/105380...
38600/105380...
39600/105380...
40600/105380...
41600/105380...
42600/105380...
43600/105380...
43600/105380...
43600/105380...
44600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/105380...
45600/

KeyboardInterrupt: 

In [131]:
metadata_api_df = pd.DataFrame(rows)
metadata_api_df

authors  category  \
0          Ramesh Narayan, Bohdan Paczyński, Tsvi Piran  astro-ph   
1                         Lawrence Krauss, Martin White  astro-ph   
2                                            J. I. Katz  astro-ph   
3                B P Schmidt, R P Kirshner, R G Eastman  astro-ph   
4                            B. J. Carrigan, J. I. Katz  astro-ph   
5          D. J. Johnson, M. W. Friedlander, J. I. Katz  astro-ph   
6                                       Valerio Faraoni  astro-ph   
7                   T. Hanawa, R. Matsumoto, K. Shibata  astro-ph   
8                                            J. I. Katz  astro-ph   
9                             A. Cappi, S. Maurogordato  astro-ph   
10                                        Rino Bandiera  astro-ph   
11                                    Peter L. Biermann  astro-ph   
12     H. T. Cho, K. -W. Ng, Achilles D. Speliotopoulos  astro-ph   
13                       Luca Amendola, Stefano Borgani  astro-ph   
14                      Mirek Giersz, Douglas C. Heggie  astro-ph   
15                          Xiaochun Luo, D. N. Schramm  astro-ph   
16             S. A. Bonometto, F. Gabbiani, A. Masiero  astro-ph   
17    Anatoly Klypin, Jon Holtzman, Joel Primack, En...  astro-ph   
18                     Karen M. Strom, Stephen E. Strom  astro-ph   
19    Peter L. Biermann, Wolfgang J. Duschl, Susanne...  astro-ph   
20       Michael Strauss, Renyue Cen, Jeremiah Ostriker  astro-ph   
21                      Michael Strauss, Daniel Koranyi  astro-ph   
22                           Avishai Dekel, Martin Rees  astro-ph   
23                      Heino Falcke, Peter L. Biermann  astro-ph   
24       Heino Falcke, Karl Mannheim, Peter L. Biermann  astro-ph   
25                                        Gary A. Mamon  astro-ph   
26                                 Geoffrey V. Bicknell  astro-ph   
27                                 Geoffrey V. Bicknell  astro-ph   
28     Baolian Cheng, David N. Schramm, James W. Truran  astro-ph   
29                     Yoshiaki SOFUE, Shigeomi YOSHIDA  astro-ph   
...                                                 ...       ...   
4970  Helen M. Johnston, Richard W. Hunstead, Garret...  astro-ph   
4971  Kevork Abazajian, Nicole F. Bell, George M. Fu...  astro-ph   
4972           M. A. Garrett, J. M. Wrobel, R. Morganti  astro-ph   
4973  Wahab Uddin, Rajmal Jain, Keiji Yoshimura, Ram...  astro-ph   
4974                     Thierry Morel, Yves Grosdidier  astro-ph   
4975  M. Ambrosio, C. Aramo, D. D'Urso, A. D. Erlyki...  astro-ph   
4976  E. Arnone, S. G. Ryan, D. Argast, J. E. Norris...  astro-ph   
4977                    J. Martin Laming, Lev Titarchuk  astro-ph   
4978                   Federica Govoni, Luigina Feretti  astro-ph   
4979                                    David Heyrovsky  astro-ph   
4980  G. Patanchon, J. -F. Cardoso, J. Delabrouille,...  astro-ph   
4981                               S. Heinz, A. Merloni  astro-ph   
4982                    Peter Englmaier, Isaac Shlosman  astro-ph   
4983                                   P. J. E. Peebles  astro-ph   
4984  P. Chris Fragile, Peter Anninos, Kyle Gustafso...  astro-ph   
4985                       M. A. Stark, Richard A. Wade  astro-ph   
4986               R. A. Wade, M. A. Stark, R. F. Green  astro-ph   
4987  Stephanie Cote, Rosemary Wyse, Claude Carignan...  astro-ph   
4988                                       Hideki Asada  astro-ph   
4989                           Poonam Chandra, Alak Ray  astro-ph   
4990  L. Boirin, M. Mendez, M. Diaz Trigo, A. N. Par...  astro-ph   
4991  P. A. James, N. S. Shane, J. H. Knapen, J. Eth...  astro-ph   
4992                 Elena Gallo, Rob Fender, Rob Hynes  astro-ph   
4993                                          Jin H. An  astro-ph   
4994                                     Maciej Konacki  astro-ph   
4995                J. Goncalves, D. Galli, M. Walmsley  astro-ph   
4996                     R. Quast, R. Baade, D

Save data frame to CSV:

In [ ]:
metadata_api_df.to_csv('arXiv_metadata_api.csv', index=False, header=True)

This is too slow. I stopped after 5000 records, after finding that there is another API to use for bulk metadata harvesting.

## Harvesting with the Open Archives Initiative:

- https://arxiv.org/help/oa/index
- http://www.openarchives.org/OAI/openarchivesprotocol.html

Differences:
- With ArXiv API, we could retrieve articles according to astro-ph subject class, e.g. astro-ph.ga, but with OAI, we cannot.

In [168]:
url = 'http://export.arxiv.org/oai2?verb=ListSets'
results = urllib.request.urlopen(url).read()
soup = BeautifulSoup(results, 'xml')
sets = soup.find_all('setSpec')
for s in sets:
    print(s.text)

cs
econ
eess
math
physics
physics:astro-ph
physics:cond-mat
physics:gr-qc
physics:hep-ex
physics:hep-lat
physics:hep-ph
physics:hep-th
physics:math-ph
physics:nlin
physics:nucl-ex
physics:nucl-th
physics:physics
physics:quant-ph
q-bio
q-fin
stat


We are interested in the `physics:astro-ph` set. 

In [238]:
url = 'http://export.arxiv.org/oai2?verb=ListRecords&set=physics:astro-ph&metadataPrefix=arXiv'
results = urllib.request.urlopen(url).read()
soup = BeautifulSoup(results, 'xml')
resumptionToken = soup.find('resumptionToken')
print('Number of article records obtained: ' + str(len(soup.find_all('record'))))
print('Total number of articles: ' + str(resumptionToken['completeListSize']))
print('Resumption token: ' + resumptionToken.string)
print('Date that we made this request: ' + soup.find('responseDate').string)
print()

print(soup.prettify())

Number of article identifiers obtained: 1000
Total number of articles: 250047
Resumption token: 3350519|1001
Date that we made this request: 2019-02-08T20:08:02Z

<?xml version="1.0" encoding="utf-8"?>
<OAI-PMH xmlns="http://www.openarchives.org/OAI/2.0/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.openarchives.org/OAI/2.0/ http://www.openarchives.org/OAI/2.0/OAI-PMH.xsd">
 <responseDate>
  2019-02-08T20:08:02Z
 </responseDate>
 <request metadataPrefix="arXiv" set="physics:astro-ph" verb="ListRecords">
  http://export.arxiv.org/oai2
 </request>
 <ListRecords>
  <record>
   <header>
    <identifier>
     oai:arXiv.org:0704.0009
    </identifier>
    <datestamp>
     2010-03-18
    </datestamp>
    <setSpec>
     physics:astro-ph
    </setSpec>
   </header>
   <metadata>
    <arXiv xmlns="http://arxiv.org/OAI/arXiv/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://arxiv.org/OAI/arXiv/ http://arxiv.org/OAI/arXiv.xsd

As it returns only 10k identifiers, we need to get the rest through a batch approach using `resumptionToken`. We also need to pause ~20s, otherwise we get a status `503` error.

https://academia.stackexchange.com/questions/38969/getting-a-dump-of-arxiv-metadata
http://www.openarchives.org/OAI/2.0/openarchivesprotocol.htm#HTTPResponseFormat

In [261]:
url = 'http://export.arxiv.org/oai2?verb=ListRecords&set=physics:astro-ph&metadataPrefix=arXiv'
resumptionToken = 'placeholder'
responseDate = None
rows = []

while resumptionToken is not None:
    # Send query and receive results
    results = urllib.request.urlopen(url).read()
    
    # Parse with Beautiful Soup
    soup = BeautifulSoup(results, 'xml')
    records = soup.find_all('record')
    for record in records:
        # Get header data
        identifier = record.find('identifier')
        datestamp = record.find('datestamp')
        spec = record.find('setSpec')
        
        # Get metadata
        filename = record.find('id')
        created = record.find('created')
        updated = record.find('updated')
        authors = []
        for author in record.find_all('author'):
            forenames = author.forenames
            keyname = author.keyname
            if forenames and keyname:
                authors.append(author.forenames.text.strip() + ' ' + author.keyname.text.strip())
        author_str = ', '.join(authors)
        title = record.find('title')
        categories = record.find('categories')
        journal = record.find('journal-ref')
        doi = record.find('doi')
        abstract = record.find('abstract')
        comments = record.find('comment')

        # Add record as row
        row = {
            'identifier': getattr(identifier, 'text', None),
            'filename': getattr(filename, 'text', None),
            'spec': getattr(spec, 'text', None),
            'title': getattr(title, 'text', None),
            'datestamp': getattr(datestamp, 'text', None),
            'created': getattr(created, 'text', None),
            'updated': getattr(updated, 'text', None), # may have more than one instance that we're missing
            'authors': authors,
            'categories': getattr(categories, 'text', None),
            'journal': getattr(journal, 'text', None),
            'doi': getattr(doi, 'text', None),
            'abstract': getattr(abstract, 'text', None),
            'comments': getattr(comments, 'text', None)
        }
        rows.append(row)
        
    # Get resumption token if provided
    resumptionToken = soup.find('resumptionToken')
    
    # Continue if we have resumption token
    if resumptionToken is not None:
        print(str(len(rows)) +'/' + str(resumptionToken['completeListSize']) + '...')
        resumptionToken = resumptionToken.text
        url = 'http://export.arxiv.org/oai2?verb=ListRecords&resumptionToken=' + resumptionToken
        time.sleep(20) # avoid http 503 status
    else:
        # Otherwise, obtain date of last request and the while loop ends here
        responseDate = soup.find('responseDate').text

1000/250047...
2000/250047...
3000/250047...
4000/250047...
5000/250047...
6000/250047...
7000/250047...
8000/250047...
9000/250047...
10000/250047...
11000/250047...
12000/250047...
13000/250047...
14000/250047...
15000/250047...
16000/250047...
17000/250047...
18000/250047...
19000/250047...
20000/250047...
21000/250047...
22000/250047...
23000/250047...
24000/250047...
25000/250047...
26000/250047...
27000/250047...
28000/250047...
29000/250047...
30000/250047...
31000/250047...
32000/250047...
33000/250047...
34000/250047...
35000/250047...
36000/250047...
37000/250047...
38000/250047...
39000/250047...
40000/250047...
41000/250047...
42000/250047...
43000/250047...
44000/250047...
45000/250047...
46000/250047...
47000/250047...
48000/250047...
49000/250047...
50000/250047...
51000/250047...
52000/250047...
53000/250047...
54000/250047...
55000/250047...
56000/250047...
57000/250047...
58000/250047...
59000/250047...
60000/250047...
61000/250047...
62000/250047...
63000/250047...
6

Load a data frame with metadata for each astro-ph article: 

In [302]:
identifiers_df = pd.DataFrame(rows)
identifiers_df['date_retrieved'] = np.full(len(identifiers_df), responseDate)
identifiers_df['filename_parsed'] = identifiers_df['filename'].str.replace('/', '')
identifiers_df

KeyError: 'filename'

Save data frame to CSV:

In [263]:
identifiers_df.to_csv('arXiv_metadata_oai.csv', index=False, header=True)

Example reading in CSV without removing leading zeros, especially in filename:

In [301]:
opened_identifiers_df = pd.read_csv('arXiv_identifiers.csv', dtype={'filename': str})
opened_identifiers_df

abstract  \
0         We discuss the results from the combined IRA...   
1         Results from spectroscopic observations of t...   
2         The very nature of the solar chromosphere, i...   
3         We present a theoretical framework for plasm...   
4         We report on the analysis of selected single...   
5         We derive masses and radii for both componen...   
6         We show that the globular cluster mass funct...   
7         We present semi-analytical constraint on the...   
8         Context. Swift data are revolutionising our ...   
9         We report the first detection of the 6.2micr...   
10        We have performed a detailed analysis of orb...   
11        By combining high-resolution HST and wide-fi...   
12        We model the essential features of eternal i...   
13        The large quantity and high quality of moder...   
14        This paper has been withdrawn by the authors.\n   
15        We argue that the discrepancies observed in ...   
16        We investigate the acceleration and simultan...   
17        The complex Monoceros Loop SNR/Rosette Nebul...   
18        Although the Gauss-Bonnet term is a topologi...   
19        I describe the different classes of Active G...   
20        We report the discovery of 14 quasars in the...   
21        We present B, R, and Halpha imaging data of ...   
22        We present a Spitzer based census of the IC ...   
23        We present the first X-ray detection of the ...   
24        Some of the means through which the possible...   
25        We have been monitoring Supernova (SN) 1987A...   
26        We study cosmological perturbations in two-f...   
27        We present new observational results obtaine...   
28        We demonstrate that as we extrapolate the cu...   
29        A new estimation of the gamma-ray flux that ...   
...                                                   ...   
250017    In this work some probable consequences of i...   
250018    The quest for a complete theory of microphys...   
250019    It is argued that our universe happens to be...   
250020    By using a two-mode description, we show tha...   
250021    We study the fermionic vacuum energy of vacu...   
250022    The formalism of quantum mechanics produces ...   
250023    The intriguing suggestion of Tegmark (1996) ...   
250024    We study the fingerprint of the Arnol'd diff...   
250025    We discuss an experiment conducted by Nesviz...   
250026    A possible solution to the problem of provid...   
250027    We examine a situation in which an informati...   
250028    We describe a scheme of quantum mechanics in...   
250029    Electrons in a spherical ultracold quasineut...   
250030    It is pointed out that the Diosi-Penrose ans...   
250031    In this letter we study the propagation of l...   
250032    We propose a measure of interaction-induced ...   
250033    Using the SU($N$) representation of the grou...   
250034    Based on the standard transfer matrix, a for...   
250035    We report on a study of complementarity in a...   
250036    Classically the Harmonic Oscillator (HO) is ...   
250037    We investigate the Hawking effect on entangl...   
250038    Recently, H{\o}ye, Brevik, Ellingsen and Aar...   
250039    We study the variances of the coordinates of...   
250040    Schwinger's finite (D) dimensional periodic ...   
250041    It is shown that the canonical quantum field...   
250042    A non-local gauge symmetry of a complex scal...   
250043    The existence of a non-thermodynamic arrow o...   
250044    Fidelity plays a key role in quantum informa...   
250045    Newtonian dynamical systems accepting the no...   
250046    The vector Burgers equation is extended to i...   

                                                  authors  \
0       ['Paul Harvey', 'Bruno Merin', 'Tracy L. Huard...   
1       ['Nceba Mhlahlo', 'David H. Buckley', 'Vikram ...   
2       ['M. A. Loukitcheva', 'S. K. Solanki', 'S. Whi...   
3       ['A. A. Scheko

Now we have all the filenames for all of the astro-ph articles that arXiv specifies in their metadata!

## Some analyses

Find out how many articles there are in each category:

In [300]:
unique, counts = np.unique(np.concatenate(opened_identifiers_df['categories'].str.split()), return_counts=True)
print(np.asarray((unique, counts)).T)

[['acc-phys' '1']
 ['adap-org' '14']
 ['alg-geom' '3']
 ['astro-ph' '105361']
 ['astro-ph.CO' '46302']
 ['astro-ph.EP' '15193']
 ['astro-ph.GA' '34545']
 ['astro-ph.HE' '32271']
 ['astro-ph.IM' '14857']
 ['astro-ph.SR' '37369']
 ['atom-ph' '8']
 ['bayes-an' '3']
 ['chao-dyn' '74']
 ['chem-ph' '2']
 ['comp-gas' '11']
 ['cond-mat' '193']
 ['cond-mat.dis-nn' '29']
 ['cond-mat.mes-hall' '62']
 ['cond-mat.mtrl-sci' '140']
 ['cond-mat.other' '121']
 ['cond-mat.quant-gas' '76']
 ['cond-mat.soft' '78']
 ['cond-mat.stat-mech' '582']
 ['cond-mat.str-el' '57']
 ['cond-mat.supr-con' '183']
 ['cs.AI' '27']
 ['cs.CC' '4']
 ['cs.CE' '45']
 ['cs.CG' '5']
 ['cs.CL' '2']
 ['cs.CR' '1']
 ['cs.CV' '97']
 ['cs.CY' '14']
 ['cs.DB' '37']
 ['cs.DC' '148']
 ['cs.DL' '114']
 ['cs.DM' '3']
 ['cs.DS' '10']
 ['cs.GR' '18']
 ['cs.HC' '19']
 ['cs.IR' '17']
 ['cs.IT' '63']
 ['cs.LG' '87']
 ['cs.MM' '5']
 ['cs.MS' '21']
 ['cs.NA' '18']
 ['cs.NE' '28']
 ['cs.NI' '10']
 ['cs.OH' '9']
 ['cs.OS' '1']
 ['cs.PF' '17']
 ['cs